This notebook selects the non-duplicates and moves them one folder upwards

In [1]:
import pandas as pd
import numpy as np

In [2]:
d_reg_num_name={}
d_reg_num_name['01'] = 'Alaska'
d_reg_num_name['02'] = 'Western Canada & USA'
d_reg_num_name['03'] = 'Arctic Canada North'
d_reg_num_name['04'] = 'Arctic Canada South'
d_reg_num_name['05'] = 'Greenland'
d_reg_num_name['06'] = 'Iceland'
d_reg_num_name['07'] = 'Svalbard and Jan Mayen'
d_reg_num_name['08'] = 'Scandinavia'
d_reg_num_name['09'] = 'Russian Arctic'
d_reg_num_name['10'] = 'North Asia'
d_reg_num_name['11'] = 'Central Europe'
d_reg_num_name['12'] = 'Caucasus and Middle East'
d_reg_num_name['13'] = 'Central Asia'
d_reg_num_name['14'] = 'South Asia West'
d_reg_num_name['15'] = 'South Asia East'
d_reg_num_name['16'] = 'Low Latitudes'
d_reg_num_name['17'] = 'Southern Andes'
d_reg_num_name['18'] = 'New Zealand'
d_reg_num_name['19'] = 'Antarctic and Subantarctic'

###
d_reg_name_sh_num={}
d_reg_name_sh_num['Alaska'] = '01'
d_reg_name_sh_num['WesternCanada'] = '02'
d_reg_name_sh_num['ArcticCanadaN'] = '03'
d_reg_name_sh_num['ArcticCanadaS']='04'
d_reg_name_sh_num['Greenland']='05'
d_reg_name_sh_num['Iceland']='06'
d_reg_name_sh_num['Svalbard']='07'
d_reg_name_sh_num['Scandinavia']='08'
d_reg_name_sh_num['RussianArctic']='09'
d_reg_name_sh_num['NorthAsia']='10' 
d_reg_name_sh_num['CentralEurope']='11'
d_reg_name_sh_num['Caucasus']='12'
d_reg_name_sh_num['CentralAsia']='13'
d_reg_name_sh_num['SouthAsiaWest']='14'
d_reg_name_sh_num['SouthAsiaEast']='15'
d_reg_name_sh_num['LowLatitudes']='16'
d_reg_name_sh_num['SouthernAndes']='17'
d_reg_name_sh_num['NewZealand']='18'
d_reg_name_sh_num['Antarctic']='19'

In [3]:
pd_actual_runs = pd.read_csv('GloGEM_GlacierMIP3_actual_runs_Lily_list.csv')
pd_actual_runs = pd_actual_runs.melt()
pd_actual_runs['value'] = pd_actual_runs.value.astype(str)


In [4]:
mv Huss_rgi* duplicates/.

mv: cannot stat 'Huss_rgi*': No such file or directory


In [5]:
rgi_regs = []
for rgi_reg in np.arange(1,20,1):
    if rgi_reg < 10:
        rgi_reg = '0'+str(rgi_reg)
    else:
        rgi_reg = str(rgi_reg)
    rgi_regs.append(rgi_reg)

In [6]:
run=False
if run:
    rgi_reg_l = []
    gcm_l = []
    ssp_l = []
    period_l = []

    for ssp in ['ssp126','ssp370','ssp585']:
        for gcm in ['gfdl-esm4','ipsl-cm6a-lr','mpi-esm1-2-hr','mri-esm2-0','ukesm1-0-ll']:

            if ssp == 'ssp126':
                periods=['1851-1870','1901-1920','1951-1970','1995-2014','2021-2040','2041-2060','2061-2080','2081-2100']
            else:
                periods=['2021-2040','2041-2060','2061-2080','2081-2100']

            for period in periods:
                for region in rgi_regs:

                    rgi_reg_l.append(region)
                    gcm_l.append(gcm)
                    if period in ['1851-1870','1901-1920','1951-1970','1995-2014']:
                        ssp_t = 'hist'
                    else:
                        ssp_t = ssp
                    ssp_l.append(ssp_t)
                    period_l.append(period)

    pd_actual_runs['gcm'] = gcm_l
    pd_actual_runs['ssp'] = ssp_l
    pd_actual_runs['rgi_reg'] = rgi_reg_l
    pd_actual_runs['period'] = period_l
    
else:
    for l in pd_actual_runs.index:
        val = pd_actual_runs['value'].loc[l] #:
        if val =='nan':
            pass
        else:
            _,_,_,_,_,region,gcm,ssp,period_long=val.split('/')
            pd_actual_runs.loc[l,'region'] = region
            pd_actual_runs.loc[l,'rgi_reg'] = d_reg_name_sh_num[region]
            pd_actual_runs.loc[l,'gcm'] = gcm
            pd_actual_runs.loc[l,'period'] = period_long[:-7]
            if period_long[:-7] in ['1851-1870','1901-1920','1951-1970','1995-2014']:
                pd_actual_runs.loc[l,'ssp'] = 'hist'
            else:
                pd_actual_runs.loc[l,'ssp'] = ssp



In [7]:
def get_path_d(folder_path='/home/www/lschuster/glacierMIP3_analysis',
             rgi_reg='01',
             model_author='Rounce',
             period='1851-1870', gcm='gfdl-esm4', ssp='hist'):
    ''' output the regional simulation file path for the respective rgi_reg, model_author, period, gcm & ssp '''
    if (model_author == 'Rounce'):
        path = f'/home/www/drounce/regional-filled-norunaway/{rgi_reg}/{model_author}_rgi{rgi_reg}_sum_{period}_{gcm}_{ssp}.nc'
    elif ('OGGM' in model_author):
        # was corrected for missing glaciers ... (by Lilian Schuster with method of Fabien)
        if 'OGGM' in model_author and ssp == 'hist':
            ssp = 'historical'
            path =  f'{folder_path}/{model_author[:4]}/regional_filled/{rgi_reg}/{model_author}_rgi{rgi_reg}_sum_{period}_{gcm}_{ssp}_filled.nc'
        else:
            path =  f'{folder_path}/{model_author[:4]}/regional_filled/{rgi_reg}/{model_author}_rgi{rgi_reg}_sum_{period}_{gcm}_{ssp}_filled.nc'
    else:
        if gcm=='ipsl-cm6a-lr':
            if model_author=='Compagno':
                gcm='psl_cm6a-lr' # no 'i' and '_' instead of '-'
            if model_author == 'Huss':
                # also Huss has some spelling 
                gcm = 'ipsl_cm6a-lr'
        if model_author=='Kraaijenbrink':
            if ssp == 'hist':
                ssp='historical'
        path = f'{folder_path}/{model_author}/duplicates/{model_author}_rgi{rgi_reg}_sum_{period}_{gcm}_{ssp}.nc'
    return path



In [23]:
pd_sel = pd_actual_runs.loc[pd_actual_runs.gcm=='ukesm1-0-ll']
pd_sel.loc[pd_sel.rgi_reg=='01'].value.iloc[7]


'/scratch_net/vierzack06_fourth/mhuss/GlacierMIP/Alaska/ukesm1-0-ll/ssp585/2081-2100_stable'

In [27]:
pd_sel.loc[pd_sel.rgi_reg=='01'].value.iloc[4]

'/scratch_net/vierzack06_fourth/mhuss/GlacierMIP/Alaska/ukesm1-0-ll/ssp585/2021-2040_stable'

In [33]:
pd_sel.loc[pd_sel.rgi_reg=='04'].value.iloc[0]


'/scratch_net/vierzack06_fourth/mhuss/GlacierMIP/ArcticCanadaS/ukesm1-0-ll/ssp126/1851-1870_stable'

In [34]:
pd_sel.loc[pd_sel.rgi_reg=='04'].value.iloc[3]


'/scratch_net/vierzack06_fourth/mhuss/GlacierMIP/ArcticCanadaS/ukesm1-0-ll/ssp126/1995-2014_stable'

In [35]:
pd_sel.loc[pd_sel.rgi_reg=='05'].value.iloc[0]


'/scratch_net/vierzack06_fourth/mhuss/GlacierMIP/Greenland/ukesm1-0-ll/ssp126/1851-1870_stable'

In [36]:
pd_sel.loc[pd_sel.rgi_reg=='05'].value.iloc[3]


'/scratch_net/vierzack06_fourth/mhuss/GlacierMIP/Greenland/ukesm1-0-ll/ssp126/1995-2014_stable'

In [9]:
# amount of working runs
len(pd_actual_runs.where(pd_actual_runs.value != 'nan').dropna())

960

In [10]:
# amount of missing runs
len(pd_actual_runs.where(pd_actual_runs.value == 'nan').dropna(how='all'))

560

In [11]:
pd_working_runs = pd_actual_runs.where(pd_actual_runs.value != 'nan').dropna()

In [12]:
import shutil
for j in pd_working_runs.index:
    f = get_path_d(rgi_reg=pd_working_runs.loc[j]['rgi_reg'],
             model_author='Huss', period=pd_working_runs.loc[j]['period'],
             gcm=pd_working_runs.loc[j]['gcm'], ssp = pd_working_runs.loc[j]['ssp'])    

    # absolute path
    src_path = f
    dst_path = '/home/www/lschuster/glacierMIP3_analysis/Huss'
    shutil.move(src_path, dst_path)

In [13]:
import os

_, _, files = next(os.walk("/home/www/lschuster/glacierMIP3_analysis/Huss/duplicates"))
file_count = len(files)
assert file_count == len(pd_actual_runs.where(pd_actual_runs.value == 'nan').dropna(how='all'))

### OLD

In [ ]:
for l in pd_actual_runs.index:
    val = pd_actual_runs['value'].loc[l] #:
    assert val[-16:-7] == pd_actual_runs['period'].loc[l]
    assert pd_actual_runs['gcm'].loc[l] in val
    if pd_actual_runs['ssp'].loc[l] == 'hist':
        ssp_test = 'ssp126'
    else:
        ssp_test = pd_actual_runs['ssp'].loc[l]
    assert val[-23:-17] == ssp_test
    a = d_reg_num_name[pd_actual_runs['rgi_reg'].loc[l]].split()
    assert a[0] in val
    if len(a)>1:
        assert a[1] in val

